In [1]:
import pandas as pd
import altair as alt

In [277]:
# Import the power plant data, fuel names, and the rainfall data
powerplants_df = pd.read_csv(r"C:\Users\david\Documents\Green House Gas Data\powerplant_data.csv")
energytype_df = pd.read_csv(r"C:\Users\david\Documents\Green House Gas Data\energytype_data.csv")
rainfall_df = pd.read_csv(r"C:\Users\david\Documents\Green House Gas Data\rainfall_data.csv")

# Merge the power plant data and fuel names
powerplant_df = powerplants_df.merge(energytype_df, how='inner', left_on = 'AER Fuel Type Code', right_on ='AER Fuel Type Code')

# Merge the power plant data and average rain fall
powerplant_and_rain_df = powerplant_df.merge(rainfall_df, how='inner', left_on = 'year', right_on ='year')

# Group the columns and sum up total energy generation
powerplant_fuel_df = powerplant_and_rain_df.groupby(['EnergyType', 'IsRenewable', 'year', 'avg_rainfall'])[['Net Generation (Megawatthours)']].sum()

# Create the percentage changes between years
powerplant_fuel_df['pct_change'] = powerplant_fuel_df['Net Generation (Megawatthours)'].pct_change()

powerplant_fuel_df.head()

Net Generation (Megawatthours)  \
EnergyType         IsRenewable year avg_rainfall                                   
Biomass and Biogas True        2012 36.02                             225517.046   
                               2013 24.06                             263220.536   
                               2014 34.81                             278705.728   
                               2015 32.21                             268629.758   
                               2016 34.00                             270192.239   

                                                  pct_change  
EnergyType         IsRenewable year avg_rainfall              
Biomass and Biogas True        2012 36.02                NaN  
                               2013 24.06           0.167187  
                               2014 34.81           0.058830  
                               2015 32.21          -0.036153  
                               2016 34.00           0.005816

In [293]:
# Reset the table index because the hierarchy columns can't be graphed
powerplant_fuel_df.reset_index(inplace = True)

# Convert the decimals to actual percentage values, so 0.16 = 16%
powerplant_fuel_df['pct_change'] = powerplant_fuel_df['pct_change']*100
powerplant_fuel_df

EnergyType  IsRenewable  year  avg_rainfall  \
0     Biomass and Biogas         True  2012         36.02   
1     Biomass and Biogas         True  2013         24.06   
2     Biomass and Biogas         True  2014         34.81   
3     Biomass and Biogas         True  2015         32.21   
4     Biomass and Biogas         True  2016         34.00   
..                   ...          ...   ...           ...   
127  Wood and Wood Waste         True  2017         35.38   
128  Wood and Wood Waste         True  2018         28.93   
129  Wood and Wood Waste         True  2019         24.05   
130  Wood and Wood Waste         True  2020         32.77   
131  Wood and Wood Waste         True  2021         32.68   

     Net Generation (Megawatthours)  pct_change  
0                        225517.046         NaN  
1                        263220.536   16.718687  
2                        278705.728    5.882973  
3                        268629.758   -3.615272  
4                        270192.239    0.581649  
..                              ...         ...  
127                      289464.580  -15.136164  
128                      336687.130   16.313758  
129                      315810.020   -6.200745  
130                      264584.860  -16.220245  
131                      322425.790   21.861013  

[132 rows x 6 columns]

In [388]:
main_df = pd.read_csv(r"C:\Users\david\Documents\Green House Gas Data\main_data.csv")
power_ghg_df = main_df.groupby(['GHGRP Facility ID', 'year', 'AER Fuel Type Code', 'Total reported direct emissions', 'CO2 emissions (non-biogenic) ', 'Methane (CH4) emissions ', 'Nitrous Oxide (N2O) emissions '])[['Total Fuel Consumption Quantity', 'Net Generation (Megawatthours)']].sum()
power_ghg_df.reset_index(inplace = True)
new_power_ghg_df = power_ghg_df.pivot(index=['GHGRP Facility ID', 'year', 'Total reported direct emissions', 'CO2 emissions (non-biogenic) ', 'Methane (CH4) emissions ', 'Nitrous Oxide (N2O) emissions '], columns='AER Fuel Type Code', values='Net Generation (Megawatthours)')

new_power_ghg_df = new_power_ghg_df.fillna(0)
new_power_ghg_df['total_generation'] = new_power_ghg_df['COL'] + new_power_ghg_df['DFO'] + new_power_ghg_df['MLG'] + new_power_ghg_df['NG'] + new_power_ghg_df['OOG'] + new_power_ghg_df['OTH'] + new_power_ghg_df['WOC'] + new_power_ghg_df['WOO'] + new_power_ghg_df['WWW']
new_power_ghg_df.head()

# Function to calculate the percentages
def calcPercentage(overall_total, fuel_total):
  if overall_total == 0:
    return 0
  else:
    return fuel_total / overall_total

fuel_groups = ['COL', 'DFO', 'MLG', 'NG', 'OOG', 'OTH', 'WOC', 'WOO', 'WWW']

for fuel in fuel_groups:
  new_column_name = fuel + "_pct"
  new_power_ghg_df[new_column_name] = new_power_ghg_df.apply(lambda x: calcPercentage(x['total_generation'], x[fuel]), axis = 1)
    
new_power_ghg_df.reset_index(inplace = True)
new_power_ghg_df['co2_per_megawatthour'] = new_power_ghg_df['CO2 emissions (non-biogenic) '] / new_power_ghg_df['total_generation']

AER Fuel Type Code  GHGRP Facility ID  year  Total reported direct emissions  \
0                             1000001  2012                        14719.108   
1                             1000001  2013                       395314.784   
2                             1000001  2014                       333193.564   
3                             1000001  2015                       405725.952   
4                             1000001  2016                       354145.488   

AER Fuel Type Code  CO2 emissions (non-biogenic)   Methane (CH4) emissions   \
0                                         14310.3                    186.50   
1                                        394913.1                    183.25   
2                                        332854.9                    154.50   
3                                        405315.5                    187.25   
4                                        353786.0                    164.00   

AER Fuel Type Code  Nitrous Oxide (N2O) emissions   COL      DFO  MLG  \
0                                          222.308  0.0    0.000  0.0   
1                                          218.434  0.0  138.875  0.0   
2                                          184.164  0.0   66.966  0.0   
3                                          223.202  0.0  102.375  0.0   
4                                          195.488  0.0  140.232  0.0   

AER Fuel Type Code         NG  ...  COL_pct   DFO_pct  MLG_pct    NG_pct  \
0                    86622.00  ...      0.0  0.000000      0.0  1.000000   
1                   869249.13  ...      0.0  0.000160      0.0  0.999840   
2                   722985.03  ...      0.0  0.000093      0.0  0.999907   
3                   868745.62  ...      0.0  0.000118      0.0  0.999882   
4                   742206.77  ...      0.0  0.000189      0.0  0.999811   

AER Fuel Type Code  OOG_pct  OTH_pct  WOC_pct  WOO_pct  WWW_pct  \
0                       0.0      0.0      0.0      0.0      0.0   
1                       0.0      0.0      0.0      0.0      0.0   
2                       0.0      0.0      0.0      0.0      0.0   
3                       0.0      0.0      0.0      0.0      0.0   
4                       0.0      0.0      0.0      0.0      0.0   

AER Fuel Type Code  co2_per_megawatthour  
0                               0.165204  
1                               0.454243  
2                               0.460347  
3                               0.466498  
4                               0.476578  

[5 rows x 26 columns]

In [278]:
# Not being used
alt.Chart(powerplant_df).mark_area().encode(
    alt.X('year:O'),
    alt.Y('sum(Net Generation (Megawatthours)):Q').stack("normalize").axis(format=".0%"),
    alt.Color('EnergyType:N'),
).properties(width = 500, height = 400)

alt.Chart(...)

In [386]:
# Not being used
chart = alt.Chart(powerplant_df).mark_area().encode(
    alt.X('year:O'),
    alt.Y('sum(Net Generation (Megawatthours)):Q'),
    alt.Color('EnergyType:N'),
).properties(width = 500, height = 400)

text = (alt.Chart(powerplant_df).mark_text()
        .encode(
                alt.X('year:O'),
                alt.Y('sum(Net Generation (Megawatthours)):Q'),
                text='EnergyType:N'
))

#chart+text

In [283]:
# Not being used
alt.Chart(powerplant_df).mark_area().encode(
    alt.X('year:O', title = 'Year'),
    alt.Y('sum(Net Generation (Megawatthours)):Q').stack("normalize").axis(format=".0%").title('Electricity Generated (MWh)'),
    alt.Color('IsRenewable:N', title = 'Renewable Energy'),
).properties(width = 400, height = 300)

alt.Chart(...)

In [341]:
# Electricity Generation by Fuel Type Over each year
linechart = alt.Chart(powerplant_df).mark_line(
    point=True,
    strokeWidth=3,
    opacity=0.7
).transform_aggregate(
    TotalGeneration='sum(Net Generation (Megawatthours))',
    groupby=['EnergyType', 'year']
).transform_window(
    Rank='rank()',
    sort=[alt.SortField('TotalGeneration', order='descending')]
).transform_filter(
    'datum.Rank <= 50'
).encode(
    alt.X('year:N', title = 'Year'),
    alt.Y('TotalGeneration:Q', title = 'Electricity Generated (MWh)'),
    alt.Color('EnergyType:N', title = 'Fuel Used', legend=None)
).properties(
    width = 500, 
    height = 400,
    title = 'Electricity Produced By Fuel Type'
)

linetext = alt.Chart(powerplant_df).mark_text(align='left', dx=5, dy=5).transform_aggregate(
    TotalGeneration='sum(Net Generation (Megawatthours))',
    groupby=['EnergyType', 'year']
).transform_window(
    Rank='rank()',
    sort=[alt.SortField('TotalGeneration', order='descending')]
).transform_filter(
    'datum.Rank <= 50 & datum.year == 2021'
).encode(
    alt.X('year:N', title = 'Year'),
    alt.Y('TotalGeneration:Q', title = 'Electricity Generated (MWh)'),
    alt.Text('EnergyType:N'),
    opacity=alt.condition('datum.EnergyType == "Wind"', alt.value(0), alt.value(1))
).properties(
    width = 500, 
    height = 400,
    title = 'Electricity Produced By Fuel Type'
)

windtext = alt.Chart(powerplant_df).mark_text(align='left', dx=5, dy=-5).transform_aggregate(
    TotalGeneration='sum(Net Generation (Megawatthours))',
    groupby=['EnergyType', 'year']
).transform_window(
    Rank='rank()',
    sort=[alt.SortField('TotalGeneration', order='descending')]
).transform_filter(
    'datum.Rank <= 50 & datum.year == 2021'
).encode(
    alt.X('year:N', title = 'Year'),
    alt.Y('TotalGeneration:Q', title = 'Electricity Generated (MWh)'),
    alt.Text('EnergyType:N'),
    opacity=alt.condition('datum.EnergyType == "Wind"', alt.value(1), alt.value(0))
).properties(
    width = 500, 
    height = 400,
    title = 'Electricity Produced By Fuel Type'
)

plot=linechart + linetext + windtext
plot.configure_axis(
    labelAngle=0
)

alt.LayerChart(...)

In [411]:
barcharts = alt.Chart(
    powerplant_fuel_df, 
    title = 'Change in amount of Electricity Generated between Hydroelectric and Natural Gas'
).mark_bar().transform_filter(
    'datum.year != 2012 & (datum.EnergyType == "Hydroelectric Conventional" | datum.EnergyType == "Natural Gas")'
).encode(
    alt.X('year:O', title = 'Year'),
    alt.Y('pct_change:Q', title = 'Percent (%) Change'),
    alt.Color('EnergyType:N', title = 'Fuel Type'),
    alt.Column('EnergyType', title = '')
).properties(width = 250, height = 250)

hydro = alt.Chart(powerplant_fuel_df).mark_circle(size = 40).transform_filter(
    'datum.year != 2012 & (datum.EnergyType == "Hydroelectric Conventional")'
).encode(
    alt.Y('pct_change:Q', title = 'Percent (%) Change',
          scale = alt.Scale(domain=[-40,120])),
    alt.X('avg_rainfall:Q', title = 'Average Rainfall (in)',
          scale = alt.Scale(domain=[20,40])),
).properties(width = 250, height = 250)

hydro_text = alt.Chart(powerplant_fuel_df).mark_text(dx=-20, dy=5).transform_filter(
    'datum.EnergyType == "Hydroelectric Conventional" & (datum.year == 2013 | datum.year == 2019)'
).encode(
    alt.Y('pct_change:Q'),
    alt.X('avg_rainfall:Q'),
    alt.Text('year:N')
).properties(width = 250, height = 250)

hydro_plot = hydro + hydro_text + hydro.transform_regression(
    'avg_rainfall',
    'pct_change'
).mark_line(color = 'gray') 

natural_gas = alt.Chart(powerplant_fuel_df).mark_circle(
    size = 40, color = "orange"
).transform_filter(
    'datum.year != 2012 & datum.EnergyType == "Natural Gas"'
).encode(
    alt.Y('pct_change:Q', title = '',
          axis=alt.Axis(labels=False, tickSize = 0),
          scale = alt.Scale(domain=[-40,120])),
    alt.X('avg_rainfall:Q', title = 'Average Rainfall (in)',
          scale = alt.Scale(domain=[20,40]))
).properties(width = 250, height = 250)

natural_gas_text = alt.Chart(powerplant_fuel_df).mark_text(dx=-20).transform_filter(
    'datum.EnergyType == "Natural Gas" & (datum.year == 2013 | datum.year == 2019)'
).encode(
    alt.Y('pct_change:Q'),
    alt.X('avg_rainfall:Q'),
    alt.Text('year:N')
).properties(width = 250, height = 250)

natural_gas_plot = natural_gas + natural_gas_text + natural_gas.transform_regression(
    'avg_rainfall',
    'pct_change'
).mark_line(color = 'gray') 

scatterplots = alt.hconcat(hydro_plot, natural_gas_plot)
alt.vconcat(barcharts, scatterplots).configure_axis(
    labelAngle=0
)

alt.VConcatChart(...)

In [286]:
alt.Chart(powerplant_df).mark_bar().transform_aggregate(
    TotalGeneration='sum(Net Generation (Megawatthours))',
    groupby=['EnergyType']
).transform_window(
    Rank='rank()',
    sort=[alt.SortField('TotalGeneration', order='descending')]
).transform_filter(
    'datum.Rank <= 5'
).encode(
    alt.X('TotalGeneration:Q', title = 'Electricity Generaged (MWh)'),
    alt.Y('EnergyType:N', title = 'Fuel Type', sort=alt.EncodingSortField(
        field='TotalGeneration', order='descending')),
    alt.Color('EnergyType:N', title = 'Fuel Type')
).properties(
    width = 400, 
    height = 300,
    title = 'Most Common Fuel Type Used to Produce Electricity'
)

alt.Chart(...)

In [378]:
alt.Chart(powerplant_fuel_df).mark_bar().transform_filter(
    'datum.year != 2012 & (datum.EnergyType == "Hydroelectric Conventional" | datum.EnergyType == "Natural Gas")'
).encode(
    #alt.Y('year:O', title = 'Year'),
    alt.Y('pct_change:Q', title='Percent Change (%)'),
    alt.X('EnergyType:N', title = '', axis=alt.Axis(labels=False, tickSize = 0)),
    alt.Color('EnergyType', title = 'Fuel Type'),
    alt.Column('year:O', title = '')
).properties(width = 50, height = 200)

alt.Chart(...)

In [412]:
alt.Chart(powerplant_fuel_df, title = 'Change in Solar Power Generation').mark_bar(
    color = '#ffc900', 
).transform_filter(
    'datum.year != 2012 & (datum.EnergyType == "Solar")'
).encode(
    alt.Y('pct_change:Q', title = 'Percent (%) Change'),
    alt.X('year:O', title = '')
).properties(width = 300, height = 300).configure_axis(
    labelAngle=0
)

alt.Chart(...)

In [199]:
# Not being used
alt.Chart(powerplant_fuel_df).mark_circle(size = 100).transform_filter(
    'datum.year != 2012 & (datum.EnergyType == "Natural Gas")'
).encode(
    alt.X('year:O'),
    alt.Y('avg_rainfall:Q', scale = alt.Scale(domain=[20,40])),
    alt.Color('pct_change', scale = alt.Scale(scheme='redblue', domainMid=0), bin=True)
).properties(width = 300, height = 300)

alt.Chart(...)

In [270]:
# Not being used
base = alt.Chart(powerplant_fuel_df).transform_filter(
    'datum.year != 2012'
).properties(
    width=250
)

left = base.transform_filter(
    'datum.year != 2012 & datum.EnergyType == "Hydroelectric Conventional"'
).encode(
    alt.Y('year:O'),
    alt.X('pct_change:Q', scale = alt.Scale(domain=[-20, 120]))
).mark_bar().properties(title='Hydroelectric')

middle = base.encode(
    alt.Y('year:O').axis(None),
    alt.Text('year:O'),
).mark_text().properties(width=25)

right = base.transform_filter(
    'datum.year != 2012 & datum.EnergyType == "Natural Gas"'
).encode(
    alt.Y('year:O').axis(None),
    alt.X('pct_change:Q', scale = alt.Scale(domain=[-20,120]))
).mark_bar().properties(title='Natural Gas')

alt.concat(left, middle, right, spacing=5)

alt.ConcatChart(...)

In [425]:
coal = alt.Chart(new_power_ghg_df).mark_circle(
    size = 50,
    color = "gray",
    opacity = 0.4
).transform_filter(
    'datum.COL_pct > 0.75'
).encode(
    alt.X('total_generation:Q'),
    alt.Y('Total reported direct emissions:Q')
).properties(width = 300, height = 300)

natural_gas = alt.Chart(new_power_ghg_df).mark_circle(
    size = 50,
    color = "orange",
    opacity = 0.4
).transform_filter(
    'datum.NG_pct > 0.75'
).encode(
    alt.X('total_generation:Q'),
    alt.Y('Total reported direct emissions:Q')
).properties(width = 300, height = 300)

coal + natural_gas

alt.LayerChart(...)

In [428]:
coal = alt.Chart(new_power_ghg_df).mark_circle(
    size = 50,
    color = "gray"
).transform_filter(
    'datum.COL_pct > 0.75'
).encode(
    alt.X('sum(total_generation):Q'),
    alt.Y('sum(Total reported direct emissions):Q')
).properties(width = 300, height = 300)

natural_gas = alt.Chart(new_power_ghg_df).mark_circle(
    size = 50,
    color = "orange"
).transform_filter(
    'datum.NG_pct > 0.75'
).encode(
    alt.X('sum(total_generation):Q'),
    alt.Y('sum(Total reported direct emissions):Q')
).properties(width = 300, height = 300)

coal + natural_gas

alt.LayerChart(...)

In [439]:
coal = alt.Chart(new_power_ghg_df).mark_bar(
    color = "gray"
).transform_filter(
    'datum.COL_pct > 0.75'
).encode(
    alt.X('sum(total_generation):Q'),
    alt.Y('mean(co2_per_megawatthour):Q')
).properties(width = 300, height = 300)

natural_gas = alt.Chart(new_power_ghg_df).mark_bar(
    color = "orange"
).transform_filter(
    'datum.NG_pct > 0.75'
).encode(
    alt.X('sum(total_generation):Q'),
    alt.Y('mean(co2_per_megawatthour):Q')
).properties(width = 300, height = 300)

coal + natural_gas

alt.LayerChart(...)